In [6]:
import csv
import nltk
import pprint
import pandas as pd
from time import time

"""
Part 2: 
    Objective: 
    
    Step 1: Read labeled tokens and group them by defined categories.

        Input:
            |     Token       |    Category   |
            |-----------------|---------------|
            |  B-person_name  |     Person    |
            |-----------------|---------------|
            | B-location_name |    Location   |
            |-----------------|---------------|
            |   B-film_actor  |    Person     |


    Output:
    
        Objective: This list will be used for calculating centroid for categories
        entity_categories = {
            'Person'   : { 'person_name', 'film_actor' },
            'Location' : { 'location_name' }
        }
        
        Objective: This list will be used for labeling words faster. 
        Brief    : The reason for this list is that when we're labeling
        words, in order to find label we have to 'find' it in entity_categories. With this list in hand we can
        find the category without looping through entity_categories.
        entity_category_dictionary = {
            'person_name' : 'Person',
            'location_name' : 'Location',        
        }
        
        
    Step 2: Read dataset and label words with their corresponding categories.
        
        Labeling action:
            
            Corina        |  B-politician_name     ----|  Person
	        Casanova      |  I-politician_name     ----|
	        ,             |  O
	        İsviçre       |  B-person_nationality  ----| Nationality
	        Federal       |  O
	        Şansölyesidir |  B-governmental_jurisdiction_basic_title  | PersonType
	        .             |  O

        Output:
            labeled_words = {
                'Corina Casanova': 'Person',
                'İsviçre': 'Nationality',
                'Şansölyesidir' : 'PersonType',
                ..
            }

"""

"\nPart 2: \n    Objective: \n    \n    Step 1: Read labeled tokens and group them by defined categories.\n\n        Input:\n            |     Token       |    Category   |\n            |-----------------|---------------|\n            |  B-person_name  |     Person    |\n            |-----------------|---------------|\n            | B-location_name |    Location   |\n            |-----------------|---------------|\n            |   B-film_actor  |    Person     |\n\n\n    Output:\n    \n        Objective: This list will be used for calculating centroid for categories\n        entity_categories = {\n            'Person'   : { 'person_name', 'film_actor' },\n            'Location' : { 'location_name' }\n        }\n        \n        Objective: This list will be used for labeling words faster. \n        Brief    : The reason for this list is that when we're labeling\n        words, in order to find label we have to 'find' it in entity_categories. With this list in hand we can\n        find 

In [8]:
#### Helpers ####
 
# Removes token identifiers from string.
def remove_token_identifiers(raw_token):
    return raw_token.replace('B-', '').replace('I-', '')

# Checks whether token is inner.
def is_inner_token(raw_token):
    return raw_token.find('I-') != -1

In [9]:
#### STEP 1 ####

t = time()
my_printer = pprint.PrettyPrinter()

# Read file
df = pd.read_excel('data/labeled_categories.xlsx')

# Fallback category for the tokens does not belong to chosen categories
fallback_category = 'Thing'
# Main category list
category_list = [
    'Person', 'Location', 'Event', 'Organization', 'DateTime', 'PersonType', 'Currency', 'Nationality', 'Ethnicity'
]
# Initialize category-entity dictionary
entity_categories = {fallback_category : set({})}
entity_category_dictionary = {}

for category in category_list:
    entity_categories[category] = set({})

# Read Excel file and fill the dictionary
for row in df.index:
    token = remove_token_identifiers(df['Token'][row])
    token = token[:token.find(' =')]
    category = df['Category'][row]
    
    # Fallback category check
    if category == '' or category == 'Delete' or category == 'delete' or category == 'Thing' or category == 'thing':
        entity_categories[fallback_category].add(token)
        entity_category_dictionary[token] = fallback_category
        continue
    
    # Undefined category check
    if category not in category_list:
        continue
    
    # Valid category
    entity_categories[category].add(token)
    entity_category_dictionary[token] = category
                
print('Time to create entity categories: {} mins'.format(round((time() - t) / 60, 4)))

Time to create entity categories: 0.0135 mins


In [10]:
# my_printer.pprint(entity_categories)
print(entity_category_dictionary['person_name'])
# my_printer.pprint(entity_categories['Location'])

Person


In [17]:
 #### STEP 2 ####

t = time()

df = pd.DataFrame()

# Read dataset
with open("data/data_origin.DUMP", encoding="utf8") as tsv:
    
    labeled_words = []

    
    for line in csv.reader(tsv, dialect="excel-tab"):
        tokenized = line[1]
        sentence = line[2]
        
        all_words = nltk.word_tokenize(sentence)
        all_tokens = nltk.word_tokenize(tokenized)
        
        sentence_valid_tokens = []
        
        for x in range(len(all_words)):
            try:
                token_raw = all_tokens[x]
                
                if token_raw == 'O':
                    continue
                
                token = remove_token_identifiers(token_raw)
                    
                if token not in entity_category_dictionary:
                    continue
                
                # We skip inner tokens, they are handled with their begin tokens
                if is_inner_token(token_raw):
                    continue
                    
                # If we reach this point it means active token is a begin token.
                word = all_words[x]
                

                label = entity_category_dictionary[token]
                
                #print(word)
                
                # Concat the next token with begin token, if it's an inner token
                
                
                next_index = x + 1
                next_raw_token = all_tokens[next_index]
                
                # loop limiter
                counter = 0
                
                while is_inner_token(next_raw_token):
                    next_word = all_words[next_index]
                    word = word + ' ' + next_word
                    next_index += 1
                    next_raw_token = all_tokens[next_index]
                    
                    counter += 1
                    if counter == 100:
                        break
                        
                if word in labeled_words:
                    continue
                    
                df = df.append({
                    'Word': word,
                    'Label': label,
                }, ignore_index=True)
                
                labeled_words.append(word)
                
                # print(word + ' : ' + label)
            
            except IndexError:
                pass
            


print(df.head())
print('Time to label the entities: {} mins'.format(round((time() - t) / 60, 4)))

Corina Casanova : Person
İsviçre : Nationality
Şansölyesidir : PersonType
Casanova : Person
İsviçre Federal Yüksek Mahkemesi : Thing
avukat : PersonType
federal : Organization
Almanca : Thing
Fransızca : Thing
İtalyanca : Location
İspanyolca : Thing
İsviçre Dışişleri Bakanlığı : Organization
İsviçre'nin : Nationality
Gilgit Baltistan : Organization
Pakistan : Location
Urduca : Thing
Gilgit : Organization
Pakistan'ın : Location
72496 : Location
Gilgit'dir : Organization
Peştuca : Thing
Wakhi : Thing
Denton : Location
Amerika Birleşik Devletleri'nde : Nationality
Teksas : Location
Oklahoma : Location
Teksas'ın : Location
Apple'ın : Organization
sunucu : PersonType
Schiller : Person
2009'da : Thing
Mac OS X v10.5 : Thing
kullanıcı : Thing
Mac OS : Thing
Apple : Organization
Intel : Organization
PowerPC : Thing
2009 : Thing
kullanıcı lisansları : Thing
Haziran 2009'dan : Thing
kullanıcılar : Thing
OS X : Thing
x86 : Thing
bilgisayar : Organization
2006 : DateTime
Lisansın : Person
lisans :

1937 : Location
Alman : Thing
şansölye : PersonType
Konrad Hermann Josef Adenauer : Person
Ocak'ta : DateTime
Katolik : Thing
Konrad Adenauer : Person
Köln'de : Thing
Freiburg : Location
Bonn'da : Location
Hukuk : Thing
Savcılıkta : Thing
Avukat : PersonType
Köln : Thing
1904 : Location
Emma Weyer : Person
evlilikten : Thing
Konrad : Person
1905 : DateTime
1906'dan : DateTime
Adenauer : Person
Prusya : Thing
ardından : Thing
; Konrad : Person
Adenauer'in : Person
1921 : DateTime
1922 : DateTime
. : Thing
Şansölyeliğe : PersonType
1933 : DateTime
Berlin'den : Location
Şansölye : PersonType
istediler : Person
Demokrat Birliği : DateTime
1946 : DateTime
eyalet : Organization
Berlin : Location
Jon Keeyes : Person
ABD : Location
Karadağlı : Nationality
2000 Le Mans 24 Saat yarışı : Event
Yoshikatsu Kawaguchi : Person
meyve : Thing
Russell Crowe'un : Person
Ford : Organization
Christian Bale : Person
Yuma : Thing
Gönüllü Katil : Person
Jonathan Swift'in : Person
Swift'in : Person
1726 : Date

Kanada'nın : Nationality
müzisyenlerinden : PersonType
Buffalo Springfield : Person
Young : Person
Young'ın : Person
1970 : DateTime
Do n't Let It Bring You : Person
`` Southern : Person
Harvest : Person
`` , : Person
And The Damage Done `` ve : Person
Of Age : Person
Heart of Gold : Person
1975 : DateTime
Cortez The Killer : Person
1978 : Location
After The Goldrush : Thing
`` gibi : Person
Rust : Person
David Gilmour : Person
Cobain : Person
Free World : Event
Harvest Moon : Event
1970'lerin : DateTime
1994 : DateTime
Greendale : Thing
David : Person
Crosby : Person
Graham Nash : Person
Nash : Person
Stadio Guido Angelini : Location
Chieti : Thing
Calcio Chieti : Location
Stadio Vincenzo Presti : Location
Gela : Location
Gela Calcio : Location
Michael Pavone : Person
Brad Turner : Person
Games : Organization
6 Aralık 2004'te : DateTime
Stadio Porta Elisa : Location
Lucca : Thing
A.S. Lucchese Libertas : Location
1953 NBA All Star Maçı : Event
1953 : Event
Wayne : Person
Boston : Orga

yönetmeni : PersonType
Abdülmecid : Person
Nisan 1823 : DateTime
Selim : Person
Abdülmecid'in : Person
1839 : DateTime
Nizip : Location
) : Location
yenilgisinin : DateTime
1841 : Location
1853 : DateTime
1845 : DateTime
1843 : Location
Piyemonte : Location
1857 : DateTime
Avrupa'ya : Location
1854 : Location
Bulgaristan'daki : Location
konsolosları : PersonType
Beyrut : DateTime
Dolmabahçe Sarayı : Location
Beykoz : Location
Edirne : Location
Meriç : Location
Teşvikiye : Location
Valide : Person
İstanbul'daki : DateTime
Mecidiyeköy : Location
Servet : Person
Kadın Efendi : Person
V. Murad'ın : Person
Gülcemal Kadın Efendi : Person
Düzd : Person
Efendi : Person
Mihail Yevgrafoviç Saltıkov Şçedrin : Person
Petersburg'daki : Location
Amy Lee Grant : Person
Amy Grant : Person
25 Kasım 1960 : DateTime
müzisyenidir : PersonType
sanat : PersonType
sanatçı : PersonType
1982'de : Location
Age to Age : Event
Grant : Person
Grammy ödülü : Event
1991'de : DateTime
Heart in Motion : Event
sanatçıs

Başkanını : PersonType
Gordon'ın : Person
Batmobile'in : Thing
motor : Thing
ezemez : Person
evlenme : PersonType
on : Currency
Gordon'dan : Person
Michael Caine : Person
Aaron Eckhart : Person
Gary Oldman : Person
Maggie Gyllenhaal : Person
Bruce Wayne'nin : Thing
Morgan Freeman : Person
sağlayan : Person
Şirketler : Thing
Roberts : Person
Cillian Murphy : Person
Murphy : Person
Michael : Person
Carbonell : Person
Chin Han : Person
Monique Curnen : Person
Christopher Nolan : Person
yapımcılığını : Thing
Uslan : Thing
Benjamin Melniker : Thing
Kevin De La Noy : Thing
Charles Roven : Person
Emma Thomas : Person
Wally Pfister : Person
Lee Smith : Person
Nathan Crowley : Thing
Lindy Hemming : Thing
Peter Lando : Person
Mitchell : Person
Chris Corbould : Thing
dublör : PersonType
Ledger : Person
verildi . : Person
Heath Ledger'ın : Person
Mark : Person
Ruffalo : Person
Jackman : Person
Eckhart'ın : Person
Katie : Person
Queen : Person
Money : Thing
Gyllenhaal'ın : Person
McAdams : Person
E

...

pitti : Location
halka : Location
Palazzo Pitti'nin : Location
Lattice Semiconductor Corporation : Organization
Oregon'dadır : Location
Lattice : Organization
yazılımlarına : Organization
3.47 : Location
Estudiantes de La Plata : Organization
Marcus Vipsanius Agrippa'ın : Person
Pomponia Caecilia Attica'dan : Person
Vipsania'yı : Person
Gaius Asinius : Person
Gaius Asinius Gallus Saloninus : Person
Dydek : Person
üstten : Thing
pushrodlar : Thing
Çocuk fuhuşu : Thing
fuhuşuna : Thing
Eisleben : Location
Rise Against : Person
hakları rise : Person
oyun çubuğu : Thing
Çubuğu : Thing
çubuğu : Thing
Alejandro Selkirk : Thing
Pablo César Aimar : Person
Cuarto : Location
Aimar : Person
Darul Takzim : Organization
Aimar'ın : Person
şarkıcı Robbie : Person
normalde : Person
Arnold Geulincx : Person
Johannes Scottus Erigena : Person
Kiev Spor Sarayı : Location
2005 Eurovision Şarkı Yarışması'na : Event
Jeffrey Lionel Dahmer : Person
21 Mayıs 1960 : DateTime
28 Kasım 1994 : DateTime
28 Kasım 199

Heckman : Person
15 Nisan 1940 : DateTime
Kamarasına : Organization
Alpuente Emirliği : Location
Alpuente : Location
emirliğine : Location
Ocak 1903 : DateTime
2 Mayıs 1997 : DateTime
GGP : Thing
Kırgızistan Millî Futbol Takımı Kırgızistan : Organization
Valdir Pereira Didi : Person
Didi : Person
Indefatigable : Thing
Indefatigable sınıfı muharebe kruvazörüdür : Thing
Tomares : Location
27 Ağustos 1944 : DateTime
Moira Kelly : Person
Arcanine : Thing
Traian : Person
4 Kasım 1951 : DateTime
2004'dan : DateTime
Sergey Karyakin : Thing
Paul Anthelme'in : Person
12 Temmuz 1916 : DateTime
Rota : Organization
romatoid artritde : Thing
Osteoartritte : Thing
Romatoid artritte : Thing
Ventotene : Location
26 Ocak 1919 : DateTime
. 23 Ekim : DateTime
Anthony Richard : Person
Pulis : Person
Luis Royo : Person
heykeltıraşlıkta : Thing
Luis Royo'nun : Person
Olalla'da : DateTime
Royo'nun : Person
Shunsuke : Person
Marinos'un : Organization
Rama Coomaraswamy : Person
Coomaraswamy'nin : Person
cerrah

Keirrison : Person
3 Aralık 1988 : DateTime
gidene : Organization
Coritiba'daki : Organization
Palmeiras'ın : Organization
Palmeiraslı : Organization
Keirrison'un : Person
24 Nisan 2009 : DateTime
1989 Erkekler Voleybol Dünya Kupası : Event
Clarence Sonny Weems : Person
8 Temmuz 1986 : DateTime
Weems : Person
Peter Elfelt : Person
The Heavy : Person
Swaby : DateTime
Saarland Millî Futbol Takımı : Organization
Ingbert : Location
Ercan Kesal'ın : Person
Cafer Köse : Person
Gürkan Aydın : Person
büyümüş olan : Person
Ebru Ceylan'ın : Person
Hatice Aslan'ın : Person
Aslan'ın : Person
ve oyuncu : Person
Ceylan'ın : Person
Allison Jolly : Person
Sonny John Moore : Person
Highland Park'ta : DateTime
From First to Last : Person
müzik yapımcısına : PersonType
Sonny Moore'un : Person
Scary Monsters and Nice Spritesı : Event
Bangarang : Event
Kıbrıs Birinci Ligi 1980 : Event
Suriye hükûmeti : Organization
Johannes Krauser II : Thing
Kazım Ergin : Person
FC Grenchen : Organization
Grenchen : Organ

1965 Afrika Uluslar Kupası : Event
. Afrika Uluslar : Event
1963 Afrika Uluslar Kupası : Event
yenerek ilk Afrika : Event
1968 Afrika Uluslar Kupası : Event
Altın Horoz : Organization
Horoz operası : Organization
balesiz : PersonType
operaevinden : Thing
Horoz : Organization
kus : Thing
Horozun : Organization
Glazunov : Person
Gana Milli Futbol Takımı : Organization
19763 : DateTime
19765 : DateTime
19761 : DateTime
19764 : DateTime
19766 : DateTime
19769 : DateTime
197611 : DateTime
197614 : DateTime
2000 Afrika Uluslar Kupası : Event
2002 Afrika Uluslar Kupası : Event
Şikago Film Eleştirmenleri Birliği : Organization
Gunnar Nordahl : Person
19 Ekim 1921 : DateTime
Nordahl'ın : Person
Gunnar Nordahl'ın : Person
2004 Afrika Uluslar Kupası : Event
2006 Afrika Uluslar Kupası : Event
Bessa : Location
Scott Mills : Person
28 Mart 1974 : DateTime
Careca : Person
Josip Katalinski : Person
Race Driver : Event
GRID : Event
video oyunuyla : Organization
Jonathan Vincent : Person
Fed Kupası'na :

Halep Eyaleti : Location
Eyaletinden : Location
Vorukh : Location
13 Eylül 1921 : DateTime
Sakarya muharebesi : Event
Sakarya Savaşı : Event
Sakarya Savaşı'nın : Event
FK Karaorman : Organization
Karaorman'ın : Organization
Tivoli Hall : Location
HDD Olimpija Ljubljana : Location
Union Olimpija'nın : Organization
Castillon Muharebesi : Event
Castillon : Event
17 Temmuz 1453'te : DateTime
Çuhlar : Ethnicity
Étienne Capoue : Person
Aurélien Capoue'dur : Person
Capoue : Person
Toulouse'nin : Location
Euroluk : Currency
Capoue'yi : Person
Volkan Bekçi : Person
Altı Avrupa Şampiyonası : Event
basketbol şampiyonası : Event
Chock : Person
Zuerlein : Person
2011 UEFA Şampiyonlar Ligi Finali : Event
Wembley Stadyumu'nun : Event
Mutlu Dervişoğlu : Person
Mutlu'nun : Person
Polona Hercog : Person
Braunau Çağdaş Tarih Günleri : Thing
Tarih günleri : Thing
Alexander Gordon Laing : Person
Yusupov Sarayı : Location
16 Eylül 2008 : DateTime
CryEngine 2'dir : Thing
Maximum Edition : Thing
oyunculu oyun

In [19]:
print(df.head(4))
t = time()

writer = pd.ExcelWriter('data/labeled_words.xlsx', engine='xlsxwriter')

# Convert the dataframe to an XlsxWriter Excel object.
df.to_excel(writer, sheet_name='Sheet1', index=False)

# Close the Pandas Excel writer and output the Excel file.
writer.save()
print('Time to save: {} mins'.format(round((time() - t) / 60, 4)))

         Label             Word
0       Person  Corina Casanova
1  Nationality          İsviçre
2   PersonType    Şansölyesidir
3       Person         Casanova
Time to save: 0.3993 mins
